# Convolutional Neural Networks for Sentence Classification

## Preface

This is the implementation of the "Convolutional Neural Networks for Sentence Classification" paper. You can find it here: https://arxiv.org/pdf/1408.5882.pdf

## Imports

In [70]:
import tensorflow as tf
from tensorflow import keras
import numpy as np
from gensim.models import Word2Vec
import nltk

import os
import string
from random import shuffle
from functools import partial

## Load the dataset

First, I have to load the dataset. I'll use the first dataset mentioned in the paper, available at this link: https://www.cs.cornell.edu/people/pabo/movie-review-data/

I'm using v1.0 of the dataset.

In [2]:
DATASET_LOCATION = "./dataset/rt-polaritydata"

In [3]:
!ls $DATASET_LOCATION

rt-polarity.neg  rt-polarity.pos


Below I'm removing all the whitespace and all the punctuation (even if the puncuation makes sense in some cases):

In [4]:
positive_reviews = []
negative_reviews = []

with open(os.path.join(DATASET_LOCATION, "rt-polarity.pos"), encoding='latin-1') as positive_reviews_file:
    positive_review_lines = positive_reviews_file.readlines()
    for positive_review_line in positive_review_lines:
        positive_reviews.append(positive_review_line.strip().translate(str.maketrans('', '', string.punctuation)))

with open(os.path.join(DATASET_LOCATION, "rt-polarity.neg"), encoding='latin-1') as negative_reviews_file:
    negative_review_lines = negative_reviews_file.readlines()
    for negative_review_line in negative_review_lines:
        negative_reviews.append(negative_review_line.strip().translate(str.maketrans('', '', string.punctuation)))

In [5]:
positive_reviews

['the rock is destined to be the 21st centurys new  conan  and that hes going to make a splash even greater than arnold schwarzenegger  jeanclaud van damme or steven segal ',
 'the gorgeously elaborate continuation of  the lord of the rings  trilogy is so huge that a column of words cannot adequately describe cowriterdirector peter jacksons expanded vision of j  r  r  tolkiens middleearth ',
 'effective but tootepid biopic',
 'if you sometimes like to go to the movies to have fun  wasabi is a good place to start ',
 'emerges as something rare  an issue movie thats so honest and keenly observed that it doesnt feel like one ',
 'the film provides some great insight into the neurotic mindset of all comics  even those who have reached the absolute top of the game ',
 'offers that rare combination of entertainment and education ',
 'perhaps no picture ever made has more literally showed that the road to hell is paved with good intentions ',
 'steers turns in a snappy screenplay that curls a

In [6]:
positive_reviews[0]

'the rock is destined to be the 21st centurys new  conan  and that hes going to make a splash even greater than arnold schwarzenegger  jeanclaud van damme or steven segal '

In [7]:
negative_reviews

['simplistic  silly and tedious ',
 'its so laddish and juvenile  only teenage boys could possibly find it funny ',
 'exploitative and largely devoid of the depth or sophistication that would make watching such a graphic treatment of the crimes bearable ',
 'garbus discards the potential for pathological study  exhuming instead  the skewed melodrama of the circumstantial situation ',
 'a visually flashy but narratively opaque and emotionally vapid exercise in style and mystification ',
 'the story is also as unoriginal as they come  already having been recycled more times than id care to count ',
 'about the only thing to give the movie points for is bravado  to take an entirely stale concept and push it through the audiences meat grinder one more time ',
 'not so much farcical as sour ',
 'unfortunately the story and the actors are served with a hack script ',
 'all the more disquieting for its relatively gorefree allusions to the serial murders  but it falls down in its attempts to h

In [8]:
negative_reviews[0]

'simplistic  silly and tedious '

In [9]:
all_reviews = []

for positive_review in positive_reviews:
    all_reviews.append(positive_review)
    
for negative_review in negative_reviews:
    all_reviews.append(negative_review)

In [10]:
len(all_reviews)

10662

In [11]:
all_reviews

['the rock is destined to be the 21st centurys new  conan  and that hes going to make a splash even greater than arnold schwarzenegger  jeanclaud van damme or steven segal ',
 'the gorgeously elaborate continuation of  the lord of the rings  trilogy is so huge that a column of words cannot adequately describe cowriterdirector peter jacksons expanded vision of j  r  r  tolkiens middleearth ',
 'effective but tootepid biopic',
 'if you sometimes like to go to the movies to have fun  wasabi is a good place to start ',
 'emerges as something rare  an issue movie thats so honest and keenly observed that it doesnt feel like one ',
 'the film provides some great insight into the neurotic mindset of all comics  even those who have reached the absolute top of the game ',
 'offers that rare combination of entertainment and education ',
 'perhaps no picture ever made has more literally showed that the road to hell is paved with good intentions ',
 'steers turns in a snappy screenplay that curls a

Now let's convert all reviews to vectors using word2vec. For this we have to train the Word2Vec model:

Note: I have done this following the tutorial here: https://www.kaggle.com/pierremegret/gensim-word2vec-tutorial

In [12]:
w2v_model = Word2Vec(min_count=1,
                     window=10,
                     size=300,
                     sample=6e-5, 
                     alpha=0.03, 
                     min_alpha=0.0007, 
                     negative=0,
                     workers=2)

Before doing anything with a model, I'll have to tokenize the words:

In [13]:
all_reviews_words = []

# https://stackoverflow.com/questions/54929726/word2vec-vocab-results-in-just-letters-and-symbols
nltk.download('punkt') # needed for the below function to work
all_reviews_words = [nltk.word_tokenize(sentence) for sentence in nltk.sent_tokenize(all_reviews)]

[nltk_data] Downloading package punkt to /home/mislav/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


TypeError: expected string or bytes-like object

I tried the above, but it didn't work. I'll tokenize the words manually:

In [14]:
all_reviews_words = []

for review in all_reviews:
    sentence = []
    word = str()
    for letter in review:
        if letter != " ":
            word += letter
        else:
            if word: # check to see if word contains anything
                sentence.append(word)
                word = str()
    all_reviews_words.append(sentence)

In [15]:
all_reviews_words

[['the',
  'rock',
  'is',
  'destined',
  'to',
  'be',
  'the',
  '21st',
  'centurys',
  'new',
  'conan',
  'and',
  'that',
  'hes',
  'going',
  'to',
  'make',
  'a',
  'splash',
  'even',
  'greater',
  'than',
  'arnold',
  'schwarzenegger',
  'jeanclaud',
  'van',
  'damme',
  'or',
  'steven',
  'segal'],
 ['the',
  'gorgeously',
  'elaborate',
  'continuation',
  'of',
  'the',
  'lord',
  'of',
  'the',
  'rings',
  'trilogy',
  'is',
  'so',
  'huge',
  'that',
  'a',
  'column',
  'of',
  'words',
  'cannot',
  'adequately',
  'describe',
  'cowriterdirector',
  'peter',
  'jacksons',
  'expanded',
  'vision',
  'of',
  'j',
  'r',
  'r',
  'tolkiens',
  'middleearth'],
 ['effective', 'but', 'tootepid'],
 ['if',
  'you',
  'sometimes',
  'like',
  'to',
  'go',
  'to',
  'the',
  'movies',
  'to',
  'have',
  'fun',
  'wasabi',
  'is',
  'a',
  'good',
  'place',
  'to',
  'start'],
 ['emerges',
  'as',
  'something',
  'rare',
  'an',
  'issue',
  'movie',
  'thats',
  

In [16]:
w2v_model.build_vocab(all_reviews_words, progress_per=10000)

In [17]:
w2v_model.train(all_reviews_words, total_examples=w2v_model.corpus_count, epochs=30, report_delay=1)

(2957306, 5911020)

In [18]:
w2v_model.init_sims(replace=True)

Let's now experiment with the Word2Vec model:

In [19]:
w2v_model.wv.vocab

{'the': <gensim.models.keyedvectors.Vocab at 0x7fc2ce62d978>,
 'rock': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f2278>,
 'is': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f2358>,
 'destined': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f22e8>,
 'to': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f2198>,
 'be': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f2208>,
 '21st': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f2390>,
 'centurys': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f23c8>,
 'new': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f2240>,
 'conan': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f2470>,
 'and': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f2320>,
 'that': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f2518>,
 'hes': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f2438>,
 'going': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f2588>,
 'make': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f24e0>,
 'a': <gensim.models.keyedvectors.Vocab at 0x7fc2cd9f25

In [20]:
w2v_model.wv.most_similar(positive=["rock"])

[('glorifying', 0.23136374354362488),
 ('competitive', 0.22535210847854614),
 ('show', 0.20936286449432373),
 ('criticizing', 0.20772430300712585),
 ('gradeschool', 0.20343244075775146),
 ('chaplins', 0.20180250704288483),
 ('flavor', 0.2016635239124298),
 ('count', 0.19792385399341583),
 ('sieve', 0.19618594646453857),
 ('horrifying', 0.19492466747760773)]

In [21]:
w2v_model.wv.most_similar(positive=["good"])

[('vanished', 0.25077003240585327),
 ('treasures', 0.2453421950340271),
 ('alcatraz', 0.22286713123321533),
 ('relaxed', 0.21954652667045593),
 ('strength', 0.21675121784210205),
 ('province', 0.21026620268821716),
 ('ethnography', 0.21013522148132324),
 ('louder', 0.20325611531734467),
 ('insinuating', 0.198930561542511),
 ('feminism', 0.19403299689292908)]

In [22]:
w2v_model.wv.similarity("rock", 'good')

0.083533175

In [23]:
w2v_model.wv.similarity("fun", 'good')

-0.002198398

In [24]:
w2v_model.wv.doesnt_match(['good', 'fun', 'sad'])

/home/mislav/anaconda3/envs/tensorflow-dev/lib/python3.6/site-packages/gensim/models/keyedvectors.py:877: FutureWarning: arrays to stack must be passed as a "sequence" type such as list or tuple. Support for non-sequence iterables such as generators is deprecated as of NumPy 1.16 and will raise an error in the future.
  vectors = vstack(self.word_vec(word, use_norm=True) for word in used_words).astype(REAL)


'sad'

Now let's convert the reviews to vectors:

In [25]:
# https://stackoverflow.com/questions/29760935/how-to-get-vector-for-a-sentence-from-the-word2vec-of-tokens-in-sentence

sentence_vectors = []

for sentence in all_reviews_words:
    avg_vector = np.zeros(300) # 300 is the vector size
    word_count = 0
    for word in sentence:
        word_vector = w2v_model.wv[word]
        avg_vector = avg_vector + word_vector
        word_count  = word_count + 1
    avg_vector = avg_vector / word_count
    sentence_vectors.append(avg_vector)

/home/mislav/anaconda3/envs/tensorflow-dev/lib/python3.6/site-packages/ipykernel_launcher.py:12: RuntimeWarning: invalid value encountered in true_divide
  if sys.path[0] == '':


In [26]:
sentence_vectors

[array([ 2.40837620e-02, -3.68669153e-03, -1.14621154e-02, -3.57552245e-03,
        -1.32708977e-02,  2.57335429e-03,  2.53642778e-02,  1.55526053e-02,
         5.10203304e-03,  6.09169000e-03, -1.19406565e-02,  7.12100022e-03,
        -1.90467834e-02, -1.17897037e-02, -1.22139163e-02,  2.17382134e-03,
        -1.06608083e-02, -1.87754111e-03,  1.03263562e-02, -6.50331077e-05,
         7.24855584e-03,  3.08909570e-03, -1.79180376e-02, -1.96273842e-02,
         4.42842748e-03, -2.13536310e-04,  8.06898950e-03, -1.63403034e-02,
         4.04977379e-02,  7.32310921e-03, -9.25570038e-04,  3.10091827e-02,
         1.37563984e-02,  1.61502516e-02, -1.64179815e-02,  1.50524424e-02,
        -6.95757774e-03,  2.35752070e-02, -1.70760000e-02,  1.23496486e-02,
         1.64068782e-02,  2.16800844e-02, -5.52391168e-04, -2.36631998e-03,
        -3.19854033e-03, -7.06601863e-03,  6.48317069e-03, -8.89725608e-03,
         1.70329124e-03, -5.79079917e-03,  2.79469603e-02, -9.65005929e-03,
         2.6

In [27]:
sentence_vectors = np.array(sentence_vectors)

In [28]:
sentence_vectors

array([[ 0.02408376, -0.00368669, -0.01146212, ...,  0.00798111,
         0.01001418, -0.00171517],
       [-0.00865146,  0.01923647,  0.00707689, ...,  0.00781443,
         0.00206187, -0.00189496],
       [ 0.02998799,  0.01377052,  0.05698116, ...,  0.04927558,
        -0.04414334,  0.00606529],
       ...,
       [ 0.00177956, -0.0031446 , -0.00227306, ...,  0.00309909,
         0.00482117, -0.01173703],
       [-0.02681141,  0.00456773, -0.01671764, ..., -0.01606253,
         0.05054184, -0.03355755],
       [ 0.00088347,  0.04250408,  0.01720886, ...,  0.0224659 ,
        -0.01029205, -0.01987312]])

In [29]:
sentence_vectors[0]

array([ 2.40837620e-02, -3.68669153e-03, -1.14621154e-02, -3.57552245e-03,
       -1.32708977e-02,  2.57335429e-03,  2.53642778e-02,  1.55526053e-02,
        5.10203304e-03,  6.09169000e-03, -1.19406565e-02,  7.12100022e-03,
       -1.90467834e-02, -1.17897037e-02, -1.22139163e-02,  2.17382134e-03,
       -1.06608083e-02, -1.87754111e-03,  1.03263562e-02, -6.50331077e-05,
        7.24855584e-03,  3.08909570e-03, -1.79180376e-02, -1.96273842e-02,
        4.42842748e-03, -2.13536310e-04,  8.06898950e-03, -1.63403034e-02,
        4.04977379e-02,  7.32310921e-03, -9.25570038e-04,  3.10091827e-02,
        1.37563984e-02,  1.61502516e-02, -1.64179815e-02,  1.50524424e-02,
       -6.95757774e-03,  2.35752070e-02, -1.70760000e-02,  1.23496486e-02,
        1.64068782e-02,  2.16800844e-02, -5.52391168e-04, -2.36631998e-03,
       -3.19854033e-03, -7.06601863e-03,  6.48317069e-03, -8.89725608e-03,
        1.70329124e-03, -5.79079917e-03,  2.79469603e-02, -9.65005929e-03,
        2.60264265e-03, -

OK. Now let's make a TensorFlow Dataset out of these variables:

In [30]:
dataset = tf.data.Dataset.from_tensor_slices(sentence_vectors)

Now let's make the labels:

In [31]:
labels = []

for i in range(0, len(positive_reviews)):
    labels.append(1)

for i in range(0, len(negative_reviews)):
    labels.append(0)

In [32]:
len(labels)

10662

In [33]:
labels = np.array(labels)

In [34]:
counter = 0

for data in dataset:
    counter = counter + 1
    
print(counter)

10662


In [35]:
dataset_with_labels = list(zip(dataset, labels))

In [36]:
dataset_with_labels[0]

(<tf.Tensor: shape=(300,), dtype=float64, numpy=
 array([ 2.40837620e-02, -3.68669153e-03, -1.14621154e-02, -3.57552245e-03,
        -1.32708977e-02,  2.57335429e-03,  2.53642778e-02,  1.55526053e-02,
         5.10203304e-03,  6.09169000e-03, -1.19406565e-02,  7.12100022e-03,
        -1.90467834e-02, -1.17897037e-02, -1.22139163e-02,  2.17382134e-03,
        -1.06608083e-02, -1.87754111e-03,  1.03263562e-02, -6.50331077e-05,
         7.24855584e-03,  3.08909570e-03, -1.79180376e-02, -1.96273842e-02,
         4.42842748e-03, -2.13536310e-04,  8.06898950e-03, -1.63403034e-02,
         4.04977379e-02,  7.32310921e-03, -9.25570038e-04,  3.10091827e-02,
         1.37563984e-02,  1.61502516e-02, -1.64179815e-02,  1.50524424e-02,
        -6.95757774e-03,  2.35752070e-02, -1.70760000e-02,  1.23496486e-02,
         1.64068782e-02,  2.16800844e-02, -5.52391168e-04, -2.36631998e-03,
        -3.19854033e-03, -7.06601863e-03,  6.48317069e-03, -8.89725608e-03,
         1.70329124e-03, -5.79079917e-0

In [37]:
dataset_with_labels[10000]

(<tf.Tensor: shape=(300,), dtype=float64, numpy=
 array([ 3.74463686e-03, -1.04532071e-02, -8.03944799e-03, -1.20944789e-02,
         8.81735746e-03, -1.17207684e-02,  9.36947525e-03,  5.38969953e-04,
        -1.71335349e-02,  1.25973283e-02, -6.11141424e-03,  5.45414910e-04,
         1.85094594e-03, -9.09333963e-03,  5.31053387e-03, -8.09836044e-03,
         3.16459931e-03,  5.50892442e-03,  3.59098112e-03, -4.43230759e-03,
         1.95396372e-02, -8.25778984e-03,  1.50825242e-02,  5.41290765e-03,
        -2.25653290e-02,  1.71828914e-03,  3.17987406e-03,  4.38609216e-03,
         1.40959615e-02,  7.63683548e-03,  9.00549769e-03,  7.23481989e-03,
         3.05518929e-03,  1.72449285e-02,  2.08436340e-03,  2.35651614e-02,
         1.63725912e-02,  6.53417972e-03, -2.62078949e-02,  1.19284727e-02,
         6.79962389e-03, -6.69633339e-03,  2.69858063e-03, -3.24329570e-03,
        -1.40413681e-02, -3.89747911e-02,  1.46941716e-03, -1.70155217e-02,
         1.24889780e-03,  9.59716728e-0

In [38]:
dataset_with_labels[5000]

(<tf.Tensor: shape=(300,), dtype=float64, numpy=
 array([-1.30699005e-02, -2.42450628e-02,  3.41495921e-03,  3.03379479e-04,
        -2.70775891e-02, -1.56022860e-02, -2.71774609e-02,  6.61957154e-03,
        -1.04200672e-02, -1.64995520e-02, -2.41006604e-02, -2.77302129e-03,
         1.10236890e-02,  2.45011373e-02, -3.27456834e-02,  1.03619650e-02,
         8.00651975e-03,  7.00740420e-03,  8.83435136e-03, -1.51950313e-02,
        -6.33659282e-03,  1.40384852e-02,  4.47764122e-03, -1.91856499e-03,
         1.08636807e-02, -3.33691513e-02,  2.53043379e-03, -5.95881017e-03,
        -1.27864801e-02,  3.67896265e-02, -2.74196158e-03,  3.16209065e-03,
         1.50260784e-03,  1.86766261e-02,  1.80426703e-02, -8.03304534e-03,
        -1.87991961e-02,  8.86347671e-03, -2.67633398e-02,  2.45143377e-02,
         8.47909572e-04,  1.69262731e-02,  5.27111405e-03,  1.53181003e-02,
        -1.32615915e-02,  7.27662228e-03,  8.51579523e-03, -1.25862172e-02,
        -3.10768606e-03, -1.20200535e-0

Let's shuffle the dataset:

In [39]:
shuffle(dataset_with_labels)
reviews, labels = zip(*dataset_with_labels)

Now let's split the model into train, val and test:

In [40]:
TRAIN_SIZE = 0.6
VAL_SIZE = 0.2

train_reviews = reviews[:int(TRAIN_SIZE * len(reviews))]
train_labels = labels[:int(TRAIN_SIZE * len(labels))]
val_reviews = reviews[int(TRAIN_SIZE * len(reviews)):int((TRAIN_SIZE + VAL_SIZE) * len(reviews))]
val_labels = labels[int(TRAIN_SIZE * len(labels)):int((TRAIN_SIZE + VAL_SIZE) * len(labels))]
test_reviews = reviews[int((TRAIN_SIZE + VAL_SIZE) * len(reviews)):]
test_labels = labels[int((TRAIN_SIZE + VAL_SIZE) * len(labels)):]

Now let's store the data to TFRecords (for exercise sake):

Code below taken from https://www.tensorflow.org/tutorials/load_data/tfrecord:

In [59]:
# The following functions can be used to convert a value to a type compatible
# with tf.train.Example.

def _bytes_feature(value):
  """Returns a bytes_list from a string / byte."""
  if isinstance(value, type(tf.constant(0))):
    value = value.numpy() # BytesList won't unpack a string from an EagerTensor.
  return tf.train.Feature(bytes_list=tf.train.BytesList(value=[value]))

def _float_feature(value):
  """Returns a float_list from a float / double."""
  return tf.train.Feature(float_list=tf.train.FloatList(value=[value]))

def _int64_feature(value):
  """Returns an int64_list from a bool / enum / int / uint."""
  return tf.train.Feature(int64_list=tf.train.Int64List(value=[value]))

# https://stackoverflow.com/questions/47861084/how-to-store-numpy-arrays-as-tfrecord (2nd answer)
def _float_list(value):
  """Returns an int64_list from a bool / enum / int / uint list."""
  return tf.train.Feature(float_list=tf.train.FloatList(value=value))

In [60]:
def serialize_example(sentence, label):
  """
  Creates a tf.train.Example message ready to be written to a file.
  """
  # Create a dictionary mapping the feature name to the tf.train.Example-compatible
  # data type.
  feature = {
      'sentence': _float_list(sentence),
      'label': _int64_feature(label),
  }

  # Create a Features message using tf.train.Example.

  example_proto = tf.train.Example(features=tf.train.Features(feature=feature))
  return example_proto.SerializeToString()

In [61]:
serialize_example(train_reviews[0].numpy().astype(float), train_labels[0])

b'\n\xd6\t\n\x0e\n\x05label\x12\x05\x1a\x03\n\x01\x01\n\xc3\t\n\x08sentence\x12\xb6\t\x12\xb3\t\n\xb0\t\xedJ\x16\xbc]\xdd\x15\xbd\xa8\xa3\x01\xbc\xd2E\xe1\xbc\x0b\xee\x9a\xbc\xc8+\x8e;\x89\xe7\xb6<\xaa\x9b\x02=\xddyJ\xba\xb0j\x9f\xbc\xc0\x86f<\x1a\xa9\xe6\xbb\xee\x18\x8c<\xf3\x8b\xeb\xbc\xc2D;\xba|\xbb*<\xf8\x0b\xdd\xbbRDV;;-G<\nPE\xbc\xc2\x8e]\xb9\xee:\xaf<\xe0\xfb]\xbb\xed3f\xb9\t\xc3^\xbc\xaa 1\xbc\x98\xea\x03<\x19\t\x8d\xbc\x14\xab\xe2\xb9\x9c\xd6\xeb\xba\xca\xe3\xe2\xbc.\xe58\xbc\n\xf0\xaa<rl-\xba\xc4l\x8a<\xee\x85J\xbc\x12\xdb\x84<\xd4`)<\x10\xed\xb6\xbc\xe5/\xa6<\xa0\x94X\xbc\x9e%V=\xc8\xdb\x94;\xb3o\x1c\xbcM\xde\r\xbcH\xd6\':\xfdA\xd3\xbcG\xd8.<\x8d\xb5\x1c<$\xc0\xca\xbb\xa5\x1e3\xbc\xf6M\xae\xbbM;\x92;\x12_\x83<\xa3lZ;\xb0\x04\x99\xbb\xff^\xc3\xbcH\xad\x88<\xb7-o\xbc\xf1\x82P;\x8a\xe7\x02\xbc\'d\xa4<\x1c\x1d\x87;U\x90\xb9<Ym\x13\xba#\xf1\x82<\xc9\xe2o\xbc\xea\x7f\xfb\xba\xb1\x12\x85\xbc\xb1\xd5[<Bu\x13\xbc\x9eJ<\xbc\xe6\x1e(\xbc@\xb5\xf5\xbc#\x93\xe5\xbb1\xf4\x04\xbd\x1b\xb1|<

In [62]:
serialize_example(train_reviews[1].numpy().astype(int), train_labels[1])

b'\n\xd6\t\n\xc3\t\n\x08sentence\x12\xb6\t\x12\xb3\t\n\xb0\t\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00

In [63]:
example_proto = tf.train.Example.FromString(serialize_example(train_reviews[1].numpy().astype(float), train_labels[1]))
example_proto

features {
  feature {
    key: "label"
    value {
      int64_list {
        value: 0
      }
    }
  }
  feature {
    key: "sentence"
    value {
      float_list {
        value: 0.02866784669458866
        value: -0.013575952500104904
        value: 0.008524613454937935
        value: -0.0030654200818389654
        value: -0.010479973629117012
        value: -0.011348900385200977
        value: -0.0011982942232862115
        value: 0.009137526154518127
        value: -0.010760459117591381
        value: 0.005520512815564871
        value: -0.022911738604307175
        value: -0.007632648106664419
        value: 0.009080218151211739
        value: -0.012377864681184292
        value: -0.005179458763450384
        value: -0.01741280034184456
        value: 0.011835110373795033
        value: 0.016165561974048615
        value: 0.012290047481656075
        value: 0.007743263617157936
        value: -0.030711704865098
        value: 0.026844626292586327
        value: -0.005398035049

Now let's convert each example in the dataset to TensorFlow Example and write it to a file:

In [64]:
# Write the `tf.train.Example` observations to the file.

filename = "train_reviews_and_labels.tfrecord"
n_observations = len(train_labels)

with tf.io.TFRecordWriter(filename) as writer:
  for review_index in range(n_observations):
    if not np.any(np.isnan(train_reviews[review_index])): # skip the reviews that contain NaN
        example = serialize_example(train_reviews[review_index], train_labels[review_index])
        writer.write(example)

Now let's read the saved file:

In [65]:
filenames = [filename]
raw_dataset = tf.data.TFRecordDataset(filenames)
raw_dataset

<TFRecordDatasetV2 shapes: (), types: tf.string>

In [66]:
for raw_record in raw_dataset.take(3):
  example = tf.train.Example()
  example.ParseFromString(raw_record.numpy())
  print(example)

features {
  feature {
    key: "label"
    value {
      int64_list {
        value: 1
      }
    }
  }
  feature {
    key: "sentence"
    value {
      float_list {
        value: -0.0091731371358037
        value: -0.03658806160092354
        value: -0.00791255384683609
        value: -0.027499113231897354
        value: -0.018912335857748985
        value: 0.004338715225458145
        value: 0.022327201440930367
        value: 0.03188673406839371
        value: -0.0007723847520537674
        value: -0.019460052251815796
        value: 0.014070212841033936
        value: -0.007039201445877552
        value: 0.017101731151342392
        value: -0.028753256425261497
        value: -0.0007143729599192739
        value: 0.010420676320791245
        value: -0.006745811551809311
        value: 0.003269453067332506
        value: 0.012156779877841473
        value: -0.012043008580803871
        value: -0.00021129383821971714
        value: 0.021390404552221298
        value: -0.003387205

For good measure, let me do this to the validation set and the test set too:

In [67]:
# Write the `tf.train.Example` observations to the file.

filename = "val_reviews_and_labels.tfrecord"
n_observations = len(val_labels)

with tf.io.TFRecordWriter(filename) as writer:
  for review_index in range(n_observations):
    if not np.any(np.isnan(val_reviews[review_index])): # skip the reviews that contain NaN
        example = serialize_example(val_reviews[review_index], val_labels[review_index])
        writer.write(example)

In [68]:
filenames = [filename]
raw_dataset = tf.data.TFRecordDataset(filenames)
raw_dataset

<TFRecordDatasetV2 shapes: (), types: tf.string>

In [69]:
for raw_record in raw_dataset.take(3):
  example = tf.train.Example()
  example.ParseFromString(raw_record.numpy())
  print(example)

features {
  feature {
    key: "label"
    value {
      int64_list {
        value: 1
      }
    }
  }
  feature {
    key: "sentence"
    value {
      float_list {
        value: -0.017875388264656067
        value: -0.030703105032444
        value: -0.03181663528084755
        value: 0.007223102729767561
        value: -0.001313821179792285
        value: -0.04404556751251221
        value: -0.00650721974670887
        value: 0.009136488661170006
        value: 0.016537979245185852
        value: -0.009372709318995476
        value: -0.004252106882631779
        value: 0.00318196346051991
        value: -0.020636916160583496
        value: -0.006962847895920277
        value: -0.04009058699011803
        value: 0.03721087798476219
        value: -0.008948869071900845
        value: 0.0011931632179766893
        value: 0.02229483239352703
        value: 0.008672382682561874
        value: 0.004647210240364075
        value: 0.027001114562153816
        value: -0.027521373704075813

In [70]:
# Write the `tf.train.Example` observations to the file.

filename = "test_reviews_and_labels.tfrecord"
n_observations = len(test_labels)

with tf.io.TFRecordWriter(filename) as writer:
  for review_index in range(n_observations):
    if not np.any(np.isnan(test_reviews[review_index])): # skip the reviews that contain NaN
        example = serialize_example(test_reviews[review_index], test_labels[review_index])
        writer.write(example)

In [71]:
filenames = [filename]
raw_dataset = tf.data.TFRecordDataset(filenames)
raw_dataset

<TFRecordDatasetV2 shapes: (), types: tf.string>

In [72]:
for raw_record in raw_dataset.take(3):
  example = tf.train.Example()
  example.ParseFromString(raw_record.numpy())
  print(example)

features {
  feature {
    key: "label"
    value {
      int64_list {
        value: 0
      }
    }
  }
  feature {
    key: "sentence"
    value {
      float_list {
        value: -0.025344118475914
        value: -0.017915870994329453
        value: 0.004615976009517908
        value: -0.03497844561934471
        value: 0.011212578043341637
        value: -0.004723551217466593
        value: -0.02678636461496353
        value: -0.0037324102595448494
        value: 0.004756224807351828
        value: 0.01334658358246088
        value: 0.025890322402119637
        value: 0.01845124550163746
        value: 0.014536921866238117
        value: 0.008020918816328049
        value: 0.013107962906360626
        value: -0.00663173059001565
        value: -0.012222038581967354
        value: -0.021075425669550896
        value: -0.006891572382301092
        value: 0.0050636655651032925
        value: 0.007115950342267752
        value: 0.03267225995659828
        value: 0.006172900553792715


Now let's build the model.

## Model

In [41]:
model = tf.keras.Sequential([
    tf.keras.layers.Conv1D(filters=32, kernel_size=3, padding='same', activation='relu', input_shape=(1, 300)),
    tf.keras.layers.Dense(1, activation='sigmoid') # only 2 classes - positive or negative
])

In [55]:
model.compile(optimizer=keras.optimizers.SGD(), loss="binary_crossentropy", metrics=["accuracy"])

Let me convert the data to a NumPy array before calling fit():

In [75]:
train_reviews = np.array(train_reviews)
train_labels = np.array(train_labels)

val_reviews = np.array(val_reviews)
val_labels = np.array(val_labels)

In [76]:
train_reviews.shape

(6397, 300)

In [77]:
train_labels.shape

(6397,)

In [78]:
val_reviews.shape

(2132, 300)

In [79]:
val_labels.shape

(2132,)

In [80]:
train_reviews.reshape(train_reviews.shape[0], 1, train_reviews.shape[1]).shape

(6397, 1, 300)

In [81]:
# https://stackoverflow.com/questions/44978768/how-do-i-shape-my-input-data-for-use-with-conv1d-in-keras

train_reviews = train_reviews.reshape(train_reviews.shape[0], 1, train_reviews.shape[1])

In [82]:
val_reviews.reshape(val_reviews.shape[0], 1, val_reviews.shape[1]).shape

(2132, 1, 300)

In [83]:
val_reviews = val_reviews.reshape(val_reviews.shape[0], 1, val_reviews.shape[1])

In [84]:
assert not np.any(np.isnan(train_reviews))

AssertionError: 

Ooops! Looks like I have some invalid data. Let's fix that:

In [85]:
train_reviews_pruned = []
train_labels_pruned = []

for review_index, train_review in enumerate(train_reviews):
    if np.any(np.isnan(train_review)):
        continue
    else:
        train_reviews_pruned.append(train_review)
        train_labels_pruned.append(train_labels[review_index])
        
train_reviews_pruned = np.array(train_reviews_pruned)
train_labels_pruned = np.array(train_labels_pruned)

In [86]:
assert not np.any(np.isnan(train_reviews_pruned))

Let's do the same thing for the validation reviews:

In [87]:
val_reviews_pruned = []
val_labels_pruned = []

for review_index, val_review in enumerate(val_reviews):
    if np.any(np.isnan(val_review)):
        continue
    else:
        val_reviews_pruned.append(val_review)
        val_labels_pruned.append(val_labels[review_index])
        
val_reviews_pruned = np.array(val_reviews_pruned)
val_labels_pruned = np.array(val_labels_pruned)

In [88]:
assert not np.any(np.isnan(val_reviews_pruned))

In [59]:
model.fit(train_reviews_pruned, train_labels_pruned, validation_data=(val_reviews_pruned, val_labels_pruned), epochs=2000)

Epoch 1/2000
200/200 [==============================] - 1s 3ms/step - loss: 0.6912 - accuracy: 0.5746 - val_loss: 0.6914 - val_accuracy: 0.5563
Epoch 2/2000
200/200 [==============================] - 1s 3ms/step - loss: 0.6912 - accuracy: 0.5752 - val_loss: 0.6914 - val_accuracy: 0.5497
Epoch 3/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.6911 - accuracy: 0.5732 - val_loss: 0.6913 - val_accuracy: 0.5432
Epoch 4/2000
200/200 [==============================] - 1s 3ms/step - loss: 0.6911 - accuracy: 0.5769 - val_loss: 0.6913 - val_accuracy: 0.5586
Epoch 5/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.6910 - accuracy: 0.5716 - val_loss: 0.6913 - val_accuracy: 0.5746
Epoch 6/2000
200/200 [==============================] - 1s 3ms/step - loss: 0.6910 - accuracy: 0.5771 - val_loss: 0.6912 - val_accuracy: 0.5765
Epoch 7/2000
200/200 [==============================] - 1s 3ms/step - loss: 0.6909 - accuracy: 0.5777 - val_loss: 0.6912 - val_accuracy:

200/200 [==============================] - 1s 4ms/step - loss: 0.6872 - accuracy: 0.5938 - val_loss: 0.6879 - val_accuracy: 0.5882
Epoch 58/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.6871 - accuracy: 0.5931 - val_loss: 0.6877 - val_accuracy: 0.5882
Epoch 59/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.6870 - accuracy: 0.5967 - val_loss: 0.6877 - val_accuracy: 0.5872
Epoch 60/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.6869 - accuracy: 0.5902 - val_loss: 0.6875 - val_accuracy: 0.5868
Epoch 61/2000
200/200 [==============================] - 1s 6ms/step - loss: 0.6868 - accuracy: 0.5920 - val_loss: 0.6874 - val_accuracy: 0.5868
Epoch 62/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.6867 - accuracy: 0.5918 - val_loss: 0.6873 - val_accuracy: 0.5844
Epoch 63/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.6866 - accuracy: 0.5985 - val_loss: 0.6872 - val_accuracy: 0.5905

200/200 [==============================] - 1s 6ms/step - loss: 0.6803 - accuracy: 0.6063 - val_loss: 0.6818 - val_accuracy: 0.5905
Epoch 114/2000
200/200 [==============================] - 1s 6ms/step - loss: 0.6801 - accuracy: 0.6035 - val_loss: 0.6816 - val_accuracy: 0.5858
Epoch 115/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.6800 - accuracy: 0.6070 - val_loss: 0.6815 - val_accuracy: 0.5905
Epoch 116/2000
200/200 [==============================] - 1s 7ms/step - loss: 0.6798 - accuracy: 0.6059 - val_loss: 0.6814 - val_accuracy: 0.5891
Epoch 117/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.6797 - accuracy: 0.6026 - val_loss: 0.6814 - val_accuracy: 0.5962
Epoch 118/2000
200/200 [==============================] - 1s 6ms/step - loss: 0.6795 - accuracy: 0.6012 - val_loss: 0.6813 - val_accuracy: 0.5933
Epoch 119/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.6794 - accuracy: 0.6028 - val_loss: 0.6811 - val_accuracy: 

200/200 [==============================] - ETA: 0s - loss: 0.6710 - accuracy: 0.61 - 1s 3ms/step - loss: 0.6710 - accuracy: 0.6128 - val_loss: 0.6742 - val_accuracy: 0.5962
Epoch 170/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.6708 - accuracy: 0.6096 - val_loss: 0.6741 - val_accuracy: 0.5891
Epoch 171/2000
200/200 [==============================] - 1s 3ms/step - loss: 0.6705 - accuracy: 0.6129 - val_loss: 0.6741 - val_accuracy: 0.5962
Epoch 172/2000
200/200 [==============================] - 1s 3ms/step - loss: 0.6705 - accuracy: 0.6095 - val_loss: 0.6738 - val_accuracy: 0.5966
Epoch 173/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.6702 - accuracy: 0.6109 - val_loss: 0.6739 - val_accuracy: 0.5943
Epoch 174/2000
200/200 [==============================] - 1s 3ms/step - loss: 0.6701 - accuracy: 0.6093 - val_loss: 0.6736 - val_accuracy: 0.5966
Epoch 175/2000
200/200 [==============================] - 1s 3ms/step - loss: 0.6698 - accuracy: 

Epoch 225/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.6611 - accuracy: 0.6148 - val_loss: 0.6670 - val_accuracy: 0.5962
Epoch 226/2000
200/200 [==============================] - 1s 3ms/step - loss: 0.6609 - accuracy: 0.6181 - val_loss: 0.6670 - val_accuracy: 0.5985
Epoch 227/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.6608 - accuracy: 0.6171 - val_loss: 0.6668 - val_accuracy: 0.5980
Epoch 228/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.6605 - accuracy: 0.6181 - val_loss: 0.6667 - val_accuracy: 0.5962
Epoch 229/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.6601 - accuracy: 0.6103 - val_loss: 0.6669 - val_accuracy: 0.6008
Epoch 230/2000
200/200 [==============================] - 1s 6ms/step - loss: 0.6602 - accuracy: 0.6195 - val_loss: 0.6668 - val_accuracy: 0.6008
Epoch 231/2000
200/200 [==============================] - 1s 7ms/step - loss: 0.6600 - accuracy: 0.6198 - val_loss: 0.6663 -

...

Epoch 1736/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5777 - accuracy: 0.6886 - val_loss: 0.6599 - val_accuracy: 0.6201
Epoch 1737/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5788 - accuracy: 0.6910 - val_loss: 0.6565 - val_accuracy: 0.6173
Epoch 1738/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5783 - accuracy: 0.6914 - val_loss: 0.6590 - val_accuracy: 0.6220
Epoch 1739/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5785 - accuracy: 0.6931 - val_loss: 0.6572 - val_accuracy: 0.6220
Epoch 1740/2000
200/200 [==============================] - 2s 8ms/step - loss: 0.5783 - accuracy: 0.6906 - val_loss: 0.6574 - val_accuracy: 0.6168
Epoch 1741/2000
200/200 [==============================] - 1s 7ms/step - loss: 0.5776 - accuracy: 0.6908 - val_loss: 0.6565 - val_accuracy: 0.6191
Epoch 1742/2000
200/200 [==============================] - 1s 6ms/step - loss: 0.5777 - accuracy: 0.6921 - val_loss: 0

Epoch 1792/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5753 - accuracy: 0.6950 - val_loss: 0.6576 - val_accuracy: 0.6215
Epoch 1793/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5757 - accuracy: 0.6950 - val_loss: 0.6598 - val_accuracy: 0.6201
Epoch 1794/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5758 - accuracy: 0.6931 - val_loss: 0.6583 - val_accuracy: 0.6201
Epoch 1795/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5757 - accuracy: 0.6924 - val_loss: 0.6576 - val_accuracy: 0.6191
Epoch 1796/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5754 - accuracy: 0.6946 - val_loss: 0.6622 - val_accuracy: 0.6234
Epoch 1797/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5752 - accuracy: 0.6947 - val_loss: 0.6612 - val_accuracy: 0.6215
Epoch 1798/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5759 - accuracy: 0.6946 - val_loss: 0

Epoch 1848/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5728 - accuracy: 0.6964 - val_loss: 0.6570 - val_accuracy: 0.6210
Epoch 1849/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5724 - accuracy: 0.6977 - val_loss: 0.6577 - val_accuracy: 0.6196
Epoch 1850/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5727 - accuracy: 0.6969 - val_loss: 0.6574 - val_accuracy: 0.6182
Epoch 1851/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5723 - accuracy: 0.6966 - val_loss: 0.6612 - val_accuracy: 0.6205
Epoch 1852/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5726 - accuracy: 0.6980 - val_loss: 0.6590 - val_accuracy: 0.6187
Epoch 1853/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5724 - accuracy: 0.6957 - val_loss: 0.6611 - val_accuracy: 0.6187
Epoch 1854/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5720 - accuracy: 0.6978 - val_loss: 0

Epoch 1904/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5688 - accuracy: 0.7041 - val_loss: 0.6565 - val_accuracy: 0.6187
Epoch 1905/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5698 - accuracy: 0.6971 - val_loss: 0.6589 - val_accuracy: 0.6182
Epoch 1906/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5696 - accuracy: 0.6983 - val_loss: 0.6596 - val_accuracy: 0.6220
Epoch 1907/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5692 - accuracy: 0.6999 - val_loss: 0.6594 - val_accuracy: 0.6144
Epoch 1908/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5694 - accuracy: 0.6977 - val_loss: 0.6574 - val_accuracy: 0.6168
Epoch 1909/2000
200/200 [==============================] - 1s 6ms/step - loss: 0.5698 - accuracy: 0.6986 - val_loss: 0.6577 - val_accuracy: 0.6187
Epoch 1910/2000
200/200 [==============================] - 1s 7ms/step - loss: 0.5695 - accuracy: 0.6969 - val_loss: 0

Epoch 1960/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5665 - accuracy: 0.7024 - val_loss: 0.6583 - val_accuracy: 0.6220
Epoch 1961/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5664 - accuracy: 0.6997 - val_loss: 0.6597 - val_accuracy: 0.6168
Epoch 1962/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5662 - accuracy: 0.7022 - val_loss: 0.6586 - val_accuracy: 0.6205
Epoch 1963/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5664 - accuracy: 0.6967 - val_loss: 0.6595 - val_accuracy: 0.6154
Epoch 1964/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5664 - accuracy: 0.7018 - val_loss: 0.6586 - val_accuracy: 0.6220
Epoch 1965/2000
200/200 [==============================] - 1s 5ms/step - loss: 0.5655 - accuracy: 0.7018 - val_loss: 0.6641 - val_accuracy: 0.6215
Epoch 1966/2000
200/200 [==============================] - 1s 4ms/step - loss: 0.5661 - accuracy: 0.7025 - val_loss: 0

I reach ~62% accuracy on the validation set and ~70% accuracy on the training set, while in the paper they reach ~80% accuracy. They apply max-pooling and dropout on the penultimate layer. I will try this model out after I save this one.

Let me save the model (https://www.tensorflow.org/tutorials/keras/save_and_load#save_the_entire_model):

In [60]:
!mkdir -p saved_model

In [61]:
model.save('saved_model/my_model')

Instructions for updating:
If using Keras pass *_constraint arguments to layers.
INFO:tensorflow:Assets written to: saved_model/my_model/assets


In [62]:
new_model = tf.keras.models.load_model('saved_model/my_model')

In [63]:
new_model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv1d (Conv1D)              (None, 1, 32)             28832     
_________________________________________________________________
dense (Dense)                (None, 1, 1)              33        
Total params: 28,865
Trainable params: 28,865
Non-trainable params: 0
_________________________________________________________________


In [64]:
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv1d (Conv1D)              (None, 1, 32)             28832     
_________________________________________________________________
dense (Dense)                (None, 1, 1)              33        
Total params: 28,865
Trainable params: 28,865
Non-trainable params: 0
_________________________________________________________________


OK, all is good, model is saved. Let's create a model with more convolutional layers, dropout on the penultimate layer and max pooling between convolutions:

In [76]:
model = tf.keras.Sequential([
    tf.keras.layers.Conv1D(filters=32, kernel_size=3, padding='same', activation='relu', input_shape=(1, 300)),
    tf.keras.layers.MaxPooling1D(padding='same'),
    tf.keras.layers.Conv1D(filters=16, kernel_size=3, padding='same', activation='relu'),
    tf.keras.layers.MaxPooling1D(padding='same'),
    tf.keras.layers.Dropout(0.2),
    tf.keras.layers.Conv1D(filters=8, kernel_size=3, padding='same', activation='relu'),
    tf.keras.layers.MaxPooling1D(padding='same'),
    tf.keras.layers.Dense(1, activation='sigmoid') # only 2 classes - positive or negative
])

In [79]:
model.compile(optimizer=keras.optimizers.Adam(), loss="binary_crossentropy", metrics=["accuracy"])

I'll also add in some callbacks to the fit method:

In [84]:
early_stopping_callback = tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=3)
model_checkpoint_callback = tf.keras.callbacks.ModelCheckpoint("saved_model_with_dropout_and_maxpooling")

model.fit(train_reviews_pruned, train_labels_pruned, validation_data=(val_reviews_pruned, val_labels_pruned), epochs=20, callbacks=[early_stopping_callback, model_checkpoint_callback])

Epoch 1/20
200/200 [==============================] - 4s 18ms/step - loss: 0.0408 - accuracy: 0.9880 - val_loss: 2.6549 - val_accuracy: 0.5962
Epoch 2/20
200/200 [==============================] - 4s 19ms/step - loss: 0.0257 - accuracy: 0.9908 - val_loss: 2.6574 - val_accuracy: 0.5929
Epoch 3/20
200/200 [==============================] - 3s 16ms/step - loss: 0.0269 - accuracy: 0.9908 - val_loss: 2.7002 - val_accuracy: 0.5886
Epoch 4/20
200/200 [==============================] - 5s 23ms/step - loss: 0.0238 - accuracy: 0.9923 - val_loss: 2.7624 - val_accuracy: 0.5821


Now the training accuracy is close to 1, but validation accuracy is about 60%. I am not sure if they specified which accuracy they were measuring in the paper. I assume they measured the validation or the test accuracy, but I'm going to stop here.

In [82]:
!mkdir -p saved_model_with_dropout_and_maxpooling

In [83]:
model.save('saved_model_with_dropout_and_maxpooling/my_model')

INFO:tensorflow:Assets written to: saved_model_with_dropout_and_maxpooling/my_model/assets


Let's load the model evaluate it on the test set:

In [41]:
model = tf.keras.models.load_model('saved_model_with_dropout_and_maxpooling/my_model')

First I have to reshape the test_reviews, then prune them to get rid of the possible NaN's:

In [43]:
test_reviews = np.array(test_reviews)

In [44]:
test_reviews = test_reviews.reshape(test_reviews.shape[0], 1, test_reviews.shape[1])

In [45]:
test_reviews_pruned = []
test_labels_pruned = []

for review_index, test_review in enumerate(test_reviews):
    if np.any(np.isnan(test_review)):
        continue
    else:
        test_reviews_pruned.append(test_review)
        test_labels_pruned.append(test_labels[review_index])
        
test_reviews_pruned = np.array(test_reviews_pruned)
test_labels_pruned = np.array(test_labels_pruned)

In [46]:
assert not np.any(np.isnan(test_reviews_pruned))

In [47]:
results = model.evaluate(test_reviews_pruned, test_labels_pruned, batch_size=128)

17/17 [==============================] - 0s 4ms/step - loss: 3.7057 - accuracy: 0.4911


Accuracy of about 49%... Well, that's worse than random guessing. I'll leave it be here, but something fishy is definitely going on here. Going further, I could try re-training the model and experimenting with various hyperparameters (number of layers, layer hyperparameters etc.).

## Extra drills

Let me try loading the TFRecords data and training the model on that data:

In [50]:
filename = "train_reviews_and_labels.tfrecord"

filenames = [filename]
train_dataset = tf.data.TFRecordDataset(filenames)
train_dataset

<TFRecordDatasetV2 shapes: (), types: tf.string>

In [57]:
for raw_record in raw_dataset.take(1):
  example = tf.train.Example()
  example.ParseFromString(raw_record.numpy())
  print(example)

features {
  feature {
    key: "label"
    value {
      int64_list {
        value: 1
      }
    }
  }
  feature {
    key: "sentence"
    value {
      float_list {
        value: -0.0091731371358037
        value: -0.03658806160092354
        value: -0.00791255384683609
        value: -0.027499113231897354
        value: -0.018912335857748985
        value: 0.004338715225458145
        value: 0.022327201440930367
        value: 0.03188673406839371
        value: -0.0007723847520537674
        value: -0.019460052251815796
        value: 0.014070212841033936
        value: -0.007039201445877552
        value: 0.017101731151342392
        value: -0.028753256425261497
        value: -0.0007143729599192739
        value: 0.010420676320791245
        value: -0.006745811551809311
        value: 0.003269453067332506
        value: 0.012156779877841473
        value: -0.012043008580803871
        value: -0.00021129383821971714
        value: 0.021390404552221298
        value: -0.003387205

In [51]:
model = tf.keras.Sequential([
    tf.keras.layers.Conv1D(filters=32, kernel_size=3, padding='same', activation='relu', input_shape=(1, 300)),
    tf.keras.layers.Dense(1, activation='sigmoid') # only 2 classes - positive or negative
])

In [52]:
model.compile(optimizer=keras.optimizers.SGD(), loss="binary_crossentropy", metrics=["accuracy"])

Below code taken from https://keras.io/examples/keras_recipes/tfrecord/:

In [111]:
def read_tfrecord(example, labeled):
    tfrecord_format = (
        {
            "sentence": tf.io.FixedLenFeature([300], tf.int64),
            "label": tf.io.FixedLenFeature([], tf.int64),
        }
        if labeled
        else {"sentence": tf.io.FixedLenFeature([300], tf.int64)}
    )
    example = tf.io.parse_single_example(example, tfrecord_format)
    if labeled:
        return example["sentence"].numpy().reshape(example["sentence"].numpy().shape[0], 1, example["sentence"].numpy().shape[1]), example["label"]
    return example["sentence"]


In [112]:
AUTOTUNE = tf.data.experimental.AUTOTUNE

In [113]:
def load_dataset(filenames, labeled=True):
    ignore_order = tf.data.Options()
    ignore_order.experimental_deterministic = False  # disable order, increase speed
    dataset = tf.data.TFRecordDataset(
        filenames
    )  # automatically interleaves reads from multiple files
    dataset = dataset.with_options(
        ignore_order
    )  # uses data as soon as it streams in, rather than in its original order
    dataset = dataset.map(
        partial(read_tfrecord, labeled=labeled), num_parallel_calls=AUTOTUNE
    )
    # returns a dataset of (image, label) pairs if labeled=True or just images if labeled=False
    return dataset


In [114]:
BATCH_SIZE = 64

In [115]:
def get_dataset(filenames, labeled=True):
    dataset = load_dataset(filenames, labeled=labeled)
    dataset = dataset.shuffle(2048)
    dataset = dataset.prefetch(buffer_size=AUTOTUNE)
    dataset = dataset.batch(BATCH_SIZE)
    return dataset

In [116]:
tf.compat.v1.enable_eager_execution()

train_dataset = get_dataset("train_reviews_and_labels.tfrecord")

AttributeError: in user code:

    <ipython-input-111-f782746dfe87>:12 read_tfrecord  *
        return example["sentence"].numpy().reshape(example["sentence"].numpy().shape[0], 1, example["sentence"].numpy().shape[1]), example["label"]

    AttributeError: 'Tensor' object has no attribute 'numpy'


### Note: Looks like the error above is related to TensorFlow (https://stackoverflow.com/questions/34097281/convert-a-tensor-to-numpy-array-in-tensorflow). I tried to fix it via various Stack Overflow suggestions, but none of them panned out.

### TODO: Fix the above error

Let me try saving the dataset to multiple .tfrecords files:

In [117]:
# The following functions can be used to convert a value to a type compatible
# with tf.train.Example.

def _bytes_feature(value):
  """Returns a bytes_list from a string / byte."""
  if isinstance(value, type(tf.constant(0))):
    value = value.numpy() # BytesList won't unpack a string from an EagerTensor.
  return tf.train.Feature(bytes_list=tf.train.BytesList(value=[value]))

def _float_feature(value):
  """Returns a float_list from a float / double."""
  return tf.train.Feature(float_list=tf.train.FloatList(value=[value]))

def _int64_feature(value):
  """Returns an int64_list from a bool / enum / int / uint."""
  return tf.train.Feature(int64_list=tf.train.Int64List(value=[value]))

# https://stackoverflow.com/questions/47861084/how-to-store-numpy-arrays-as-tfrecord (2nd answer)
def _float_list(value):
  """Returns an int64_list from a bool / enum / int / uint list."""
  return tf.train.Feature(float_list=tf.train.FloatList(value=value))

In [118]:
def serialize_example(sentence, label):
  """
  Creates a tf.train.Example message ready to be written to a file.
  """
  # Create a dictionary mapping the feature name to the tf.train.Example-compatible
  # data type.
  feature = {
      'sentence': _float_list(sentence),
      'label': _int64_feature(label),
  }

  # Create a Features message using tf.train.Example.

  example_proto = tf.train.Example(features=tf.train.Features(feature=feature))
  return example_proto.SerializeToString()

In [121]:
# Write the `tf.train.Example` observations to 10 files.

base_filename = "train_reviews_and_labels"
n_observations = int(len(train_labels) / 10)
last_observation_index = 0

for filename_index in range(1, 11):
  with tf.io.TFRecordWriter(base_filename + "_" + str(filename_index) + ".tfrecord") as writer:
    for review_index in range(last_observation_index, last_observation_index + n_observations):
      last_observation_index = last_observation_index + 1
      if not np.any(np.isnan(train_reviews[review_index])): # skip the reviews that contain NaN
        example = serialize_example(train_reviews[review_index], train_labels[review_index])
        writer.write(example)

Now let's read some of the saved files:

In [124]:
filenames = ["train_reviews_and_labels_1.tfrecord", "train_reviews_and_labels_6.tfrecord"]
raw_dataset = tf.data.TFRecordDataset(filenames)
raw_dataset

<TFRecordDatasetV2 shapes: (), types: tf.string>

In [125]:
for raw_record in raw_dataset.shuffle(256).take(3):
  example = tf.train.Example()
  example.ParseFromString(raw_record.numpy())
  print(example)

features {
  feature {
    key: "label"
    value {
      int64_list {
        value: 1
      }
    }
  }
  feature {
    key: "sentence"
    value {
      float_list {
        value: 0.0018746330169960856
        value: 0.025759704411029816
        value: -0.03320995345711708
        value: -0.00801225658506155
        value: -0.06313794106245041
        value: -0.004773209802806377
        value: -0.013178729452192783
        value: -0.0015723208198323846
        value: -0.03933947533369064
        value: -0.022896677255630493
        value: -0.017550675198435783
        value: 0.04785221442580223
        value: -0.01819681189954281
        value: -0.0014014507178217173
        value: 0.004016422666609287
        value: 0.01130150817334652
        value: 0.038305480033159256
        value: 0.02719438262283802
        value: 0.032129012048244476
        value: -0.046991363167762756
        value: 0.013681294396519661
        value: 0.03670224919915199
        value: 0.0484192855656147

OK, so that's how I would split the dataset into multiple TFRecords files.